## OpenStreetMap Data Wrangling with SQL - San Francisco Area

In this project I am using the .OSM file from OpenStreetMap for the San Francisco metropolian area, audit and clean the information, create CSV files for nodes, ways, and their tags; and finally use SQL to get queries on the data.

The data is downloaded from:
https://mapzen.com/data/metro-extracts/metro/san-francisco_california/

### Table of contents:
1. Audit and clean the data   
    1.1. Street names   
    1.2. Postcodes 
2. More cleanup  
    2.1. Deal with empty 'uid' fields   
    2.2. Deal with empty nodes and ways values  
3. Create CSV files for nodes, ways, and their tags    
4. Adding the CSV files to the database   
    4.1. Adding huge files to the database (nodes and ways tables)
5. Getting queries from the database   
6. Additional suggestions for improving and analyzing the data   
    6.1. Benefits and anticipated problems in implementing the improvements

### Auditing street names

Since there are many users who are entering data in OpenStreetMap, the way they represent the formatting of streets can vary. For example, the street type 'Avenue' can be written in formats such as:
- Avenue (starting with capital letter)
- Ave
- Ave.
- avenue (starting with small letter)

To be able to process the data, we need to make these street types uniform. In case we are later searching for a specific Avenue names, we can do a quick search on all street types that have the word 'Avenue' in them and we can make sure that we are not missing anything with abrreviations of Avenue.

The code below changes all the street types in the 'mapping' list to the 'expected' list. I first go through the 'node' and 'way' element and iterate in their 'tag' element. In the tag element, I extract all types of streets that are NOT in the expcted list. Then I change all those to the format in the expected list of names.

In [1]:
#Initial imports
import xml.etree.cElementTree as ET
from collections import defaultdict
import re
import pprint

#The OSM file that I am going to use to extract the types of street from
OSMFILE = '/Users/nazaninmirarab/Desktop/Data Science/P3/Project/san-francisco_california.osm'

street_type_re = re.compile(r'\b\S+\.?$', re.IGNORECASE)

#The list of street types I will build after the code is executed
expected = ["Street", "Avenue", "Boulevard", "Drive", "Court", "Place", "Square", "Lane", "Road", 
            "Trail", "Parkway", "Commons", "Broadway", "Way", "Center", "Crescent"]

#The list of dictionaries, containing street types that need to be changed to match the expected list
mapping = { "St": "Street",
            "St.": "Street",
            "street": "Street",
            "Ave": "Avenue",
            "Ave.": "Avenue",
            "AVE": "Avenue,",
            "avenue": "Avenue",
            "Rd.": "Road",
            "Rd": "Road",
            "road": "Road",
            "Blvd": "Boulevard",
            "Blvd.": "Boulevard",
            "Blvd,": "Boulevard",
            "boulevard": "Boulevard",
            "broadway": "Broadway",
            "square": "Square",
            "way": "Way",
            "Dr.": "Drive",
            "Dr": "Drive",
            "ct": "Court",
            "Ct": "Court",
            "court": "Court",
            "Sq": "Square",
            "square": "Square",
            "cres": "Crescent",
            "Cres": "Crescent",
            "Ctr": "Center",
            "Hwy": "Highway",
            "hwy": "Highway",
            "Ln": "Lane",
            "Ln.": "Lane",
            "parkway": "Parkway"
            }

#Checking to fetch only street types that are NOT in the expected list
def audit_street_type(street_types, street_name):
    m = street_type_re.search(street_name)
    if m:
        street_type = m.group()
        if street_type not in expected:
            street_types[street_type].add(street_name)

#The 'K' attribute in the 'node' and 'way' tags with contains the street names 
def is_street_name(elem):
    return (elem.attrib['k'] == "addr:street")

#Iterating through the 'tag' element of node and way tags and adding the street names to the default dictionary
def audit(osmfile):
    osm_file = open(osmfile, "r")
    street_types = defaultdict(set)
    for event, elem in ET.iterparse(osm_file, events=("start",)):

        if elem.tag == "node" or elem.tag == "way":
            for tag in elem.iter("tag"):
                if is_street_name(tag):
                    audit_street_type(street_types, tag.attrib['v'])
    return street_types

#Changing the names of the streets to match the expected list
def update_name(name, mapping):
    output = list()
    parts = name.split(" ")
    for part in parts:
        if part in mapping:
            output.append(mapping[part])
        else:
            output.append(part)

    return " ".join(output)

#Showing the final list. On the left is the original street name and on the right the correct format 
#based on the expected list
st_types = audit(OSMFILE)
for st_type, ways in st_types.iteritems():
        for name in ways:
            better_name = update_name(name, mapping)
            print name, "=>", better_name


New Montgomery => New Montgomery
St Marys Rd => Street Marys Road
Buena Vista Rd => Buena Vista Road
Mecartney Rd => Mecartney Road
Willow Rd => Willow Road
Se Quad I-680 / Rudgear Rd => Se Quad I-680 / Rudgear Road
Ascot Rd => Ascot Road
Ygnacio Valley Rd => Ygnacio Valley Road
Marshlands Rd => Marshlands Road
Rollins Rd => Rollins Road
Market Street Suite 3658 => Market Street Suite 3658
broadway => Broadway
Alameda => Alameda
The Alameda => The Alameda
Bay and Powell => Bay and Powell
Vallejo Street Stairway => Vallejo Street Stairway
Corte Yolanda => Corte Yolanda
16th St #404 => 16th Street #404
Menlo Ave  # 4 => Menlo Avenue  # 4
Pacific Marina => Pacific Marina
San Leandro Marina => San Leandro Marina
Indian Rock Path => Indian Rock Path
Oak Street Path => Oak Street Path
Mendocino Path => Mendocino Path
Arden Path => Arden Path
Parnassus Path => Parnassus Path
Multi Use Building => Multi Use Building
Ferry Building => Ferry Building
La Loma => La Loma
E Of Center St @ I-580 => 

### Auditing postcodes

Postcodes are another inconsistent type of data that is entered into the map. The inconsistency is either in how they are represented (with the city aabreviation or without) or how long they are.

By running the code below, I found out that there are two ways the postcodes are shown in the OSM file:
1. A 5-digit format (e.g. 12345)
2. A 5-digit format followed by more numbers after a hyphen (e.g. 12345-6789)
3. A format with which the city name is mentioned in the beginning (e.g. CA 12345)

I used regular expression to extract 5-length digits from all the above postcodes. 

    ^\D*(\d{5}).*
    
- This regular expression asserts position at start of the string ( ^ ) and matches any character that is NOT a digit ( \D* )
- The ( \d{5} ) matches a digit exactly 5 times. This means for a postcode like 123456, it matched 12345
- In case the postcode starts with letters (e.g. CA 12345), it gives two groups of output: One is 'CA' and the other is '12345'. Depending on which one is needed, the preferred group can be chosen. 

In [2]:
#Initial imports
import xml.etree.cElementTree as ET
from collections import defaultdict
import re
import pprint

#The OSM file that I am going to use to extract the types of street from
OSMFILE = '/Users/nazaninmirarab/Desktop/Data Science/P3/Project/san-francisco_california.osm'

#A dictionary that contains the postcodes
def dicti(data, item):
    data[item] += 1

#Specifying which element contains the postcode
def get_postcode(elem):
    return (elem.attrib['k'] == "addr:postcode")

#Iterating through the 'node' and 'way' tag, extracting the value of the key attribute (i.e. 'K'),
#and adding them to the 'data' dictionary
def audit(osmfile):
    osm_file = open(osmfile, "r")
    data = defaultdict(int)
    for event, elem in ET.iterparse(osm_file, events=("start",)):

        if elem.tag == "node" or elem.tag == "way":
            for tag in elem.iter("tag"):
                if get_postcode(tag):
                    dicti(data, tag.attrib['v'])
    return data

#Updating the postcodes
def update_postcode(digit):
    output = list()
    if len(digit) > 5:
        search = re.match('^\D*(\d{5}).*', digit) #regulat expression catches digits with the length of 5
        new_digit = search.group(1) #I chose group 1 as it only contains digits
        output.append(new_digit)
    else:
        output.append(digit)

    return ', '.join(str(x) for x in output)

postcode_types = audit(OSMFILE)
for postcode, nums in postcode_types.iteritems():
    better_code = update_postcode(postcode)
    print postcode, "=>", better_code
    


CA 94544 => 94544
CA 94541 => 94541
94002-2121 => 94002
94121-3131 => 94121
94404 => 94404
94401 => 94401
94402 => 94402
94403 => 94403
94563 => 94563
94560 => 94560
94118 => 94118
94611 => 94611
94610 => 94610
CA 94133 => 94133
94612 => 94612
94112 => 94112
94113 => 94113
94110 => 94110
94111 => 94111
94619 => 94619
94618 => 94618
94114 => 94114
94115 => 94115
CA:94103 => 94103
95430 => 95430
90214 => 90214
94128 => 94128
94612-2202 => 94612
94127 => 94127
94579 => 94579
94124 => 94124
94123 => 94123
94122 => 94122
94121 => 94121
94129 => 94129
94577 => 94577
94606 => 94606
94607 => 94607
94605 => 94605
94602 => 94602
94603 => 94603
94601 => 94601
94044 => 94044
94801 => 94801
94804 => 94804
94805 => 94805
94608 => 94608
94609 => 94609
CA 94708 => 94708
94965 => 94965
94964 => 94964
1087 => 1087
94720-1076 => 94720
CA 94404 => 94404
94118-1316 => 94118
94130 => 94130
94131 => 94131
94132 => 94132
94133 => 94133
94134 => 94134
94549-5506 => 94549
94038 => 94038
94970 => 94970
94030 => 

### More cleanup

I found more problems in the data as I was creating the CSV files. While the validation was set to True, it made sure that the tables are being created according to the schema. 
 
1. Although according to the best practice of OpenStreetMap, all user's information like (uid and user fields) should be written while submitting data, they are not; thus, causing validation to throw errors. 

   Exception:
   Element of type 'node' has the following errors:
   [{'uid': ['required field'], 'user': ['required field']}]

   The error means that, whoever uploaded the data for the elements that generated that error, 
   they didn't follow the best practices for OpenStreetMaps and omitted to enter a 'uid' and 'user' field.
    
   To fix this issue, I had to add a try and except statement, and giving a fake value to that attribute.

    try:   
      way_attribs[item] = element.attrib[item]   
    except:   
      way_attribs[item] = "9999999"   
     
2. Another issue was with empty values for the tag_dict_node['type'] and tag_dict_way['type'] where some of the fields were empty and the validation was throwing an error.

   To fix the issue I added a conditional statement to assign value of type as 'regular' should the script not find any value to put for it. As an example,
   
     if len(character_before_colon) != 0:   
      tag_dict_way['type'] = character_before_colon[0][: -1]   
   else:   
      tag_dict_way['type'] = 'regular'   

### Explaining the shape_element function

The function takes as input an iterparse Element object and returns a dictionary.

##### If the element top level tag is "node":
The dictionary returned has the format {"node": .., "node_tags": ...}

The "node" field holds a dictionary of the following top level node attributes:   
id, user, uid, version, lat, lon, timestamp, changeset   
All other attributes are ignored

The "node_tags" field holds a list of dictionaries, one per secondary tag. Secondary tags are
child tags of node which have the tag name/type: "tag". Each dictionary has the following
fields from the secondary tag attributes:  
- id: the top level node id attribute value
- key: the full tag "k" attribute value if no colon is present or the characters after the colon if one is.
- value: the tag "v" attribute value
- type: either the characters before the colon in the tag "k" value or "regular" if a colon is not present.  
- if the tag "k" value contains problematic characters, the tag should be ignored
- if the tag "k" value contains a ":" the characters before the ":" should be set as the tag type
  and characters after the ":" should be set as the tag key
- if there are additional ":" in the "k" value they and they should be ignored and kept as part of
  the tag key. For example <tag k="addr:street:name" v="Lincoln"/> should be turned into:  
  {'id': 12345, 'key': 'street:name', 'value': 'Lincoln', 'type': 'addr'}   
- If a node has no secondary tags then the "node_tags" field should just contain an empty list.

##### If the element top level tag is "way":
The dictionary has the format {"way": ..., "way_tags": ..., "way_nodes": ...}

The "way" field should hold a dictionary of the following top level way attributes:   
id, user, uid, version, timestamp, changeset   
All other attributes are ignored

The "way_tags" field again holds a list of dictionaries, following the exact same rules as for "node_tags".

Additionally, the dictionary has a field "way_nodes". "way_nodes" holds a list of dictionaries, one for each nd child tag.  Each dictionary has the fields:    
- id: the top level element (way) id
- node_id: the ref attribute value of the nd tag
- position: the index starting at 0 of the nd tag i.e. what order the nd tag appears within the way element

In [40]:
#Initial imports
import csv
import codecs
import pprint
import re
import xml.etree.cElementTree as ET

#Running this on your local machine, you need to have these libraries installed. Use 'pip install'
import cerberus
import schema

OSM_PATH = '/Users/nazaninmirarab/Desktop/Data Science/P3/Project/san-francisco_california.osm'

NODES_PATH = "/Users/nazaninmirarab/Desktop/Data Science/P3/Project/nodes.csv"
NODE_TAGS_PATH = "/Users/nazaninmirarab/Desktop/Data Science/P3/Project/nodes_tags.csv"
WAYS_PATH = "/Users/nazaninmirarab/Desktop/Data Science/P3/Project/ways.csv"
WAY_NODES_PATH = "/Users/nazaninmirarab/Desktop/Data Science/P3/Project/ways_nodes.csv"
WAY_TAGS_PATH = "/Users/nazaninmirarab/Desktop/Data Science/P3/Project/ways_tags.csv"

LOWER_COLON = re.compile(r'^([a-z]|_)+:([a-z]|_)+')
PROBLEMCHARS = re.compile(r'[=\+/&<>;\'"\?%#$@\,\. \t\r\n]')

SCHEMA = schema.schema

# The columns in the CSV files. The same columns need to be created for the database
NODE_FIELDS = ['id', 'lat', 'lon', 'user', 'uid', 'version', 'changeset', 'timestamp']
NODE_TAGS_FIELDS = ['id', 'key', 'value', 'type']
WAY_FIELDS = ['id', 'user', 'uid', 'version', 'changeset', 'timestamp']
WAY_TAGS_FIELDS = ['id', 'key', 'value', 'type']
WAY_NODES_FIELDS = ['id', 'node_id', 'position']

#This function 
def shape_element(element, node_attr_fields=NODE_FIELDS, way_attr_fields=WAY_FIELDS,
                  problem_chars=PROBLEMCHARS, default_tag_type='regular'):
    """Clean and shape node or way XML element to Python dict"""

    node_attribs = {}
    way_attribs = {}
    way_nodes = []
    tags = []  # Handle secondary tags the same way for both node and way elements

    if element.tag == 'node':
        for item in NODE_FIELDS:
            try:
                node_attribs[item] = element.attrib[item]
            except:
                node_attribs[item] = "9999999"
                
        for tg in element.iter('tag'):
            tag_dict_node = {}
            tag_dict_node['id'] = element.attrib['id']
            tag_dict_node['value'] = tg.attrib['v']
            if ':' not in tg.attrib['k']:
                tag_dict_node['key'] = tg.attrib['k']
                tag_dict_node['type'] = 'regular'
            else:
                
                character_before_colon = re.findall('^[a-zA-Z]*:', tg.attrib['k'])
                character_after_colon = re.findall(':[a-zA-Z]+' , tg.attrib['k'])
                if len(character_after_colon) != 0:
                    tag_dict_node['key'] = character_after_colon[0][1:]
                else:
                    tag_dict_node['key'] = 'regular'

                if len(character_before_colon) != 0:
                    tag_dict_node['type'] = character_before_colon[0][: -1]
                else:
                    tag_dict_node['type'] = 'regular'
            tags.append(tag_dict_node)
            
        return {'node': node_attribs, 'node_tags': tags}
        
    elif element.tag == 'way':
        for item in WAY_FIELDS:
            try:
                way_attribs[item] = element.attrib[item]
            except:
                way_attribs[item] = "9999999"
        
        for tg in element.iter('tag'):
            tag_dict_way = {}
            tag_dict_way['id'] = element.attrib['id']
            tag_dict_way['value'] = tg.attrib['v']
            if ':' not in tg.attrib['k']:
                tag_dict_way['key'] = tg.attrib['k']
                tag_dict_way['type'] = 'regular'
            else:
                character_before_colon = re.findall('^[a-zA-Z]*:', tg.attrib['k'])
                character_after_colon = re.findall(':[a-zA-Z_]+', tg.attrib['k'])
                
                if len(character_after_colon) == 1:
                    tag_dict_way['key'] = character_after_colon[0][1:]
                if len(character_after_colon) > 1:
                    tag_dict_way['key'] = character_after_colon[0][1: ] + character_after_colon[1]
                
                if len(character_before_colon) != 0:
                    tag_dict_way['type'] = character_before_colon[0][: -1]
                else:
                    tag_dict_way['type'] = 'regular'
                
                
            tags.append(tag_dict_way)
            
        count = 0
        for tg in element.iter('nd'):
            tag_dict_nd = {}
            tag_dict_nd['id'] = element.attrib['id']
            tag_dict_nd['node_id'] = tg.attrib['ref']
            tag_dict_nd['position'] = count
            count += 1
            
            way_nodes.append(tag_dict_nd)
        
        return {'way': way_attribs, 'way_nodes': way_nodes, 'way_tags': tags}

# ================================================== #
#               Helper Functions                     #
# ================================================== #
def get_element(osm_file, tags=('node', 'way', 'relation')):
    """Yield element if it is the right type of tag"""

    context = ET.iterparse(osm_file, events=('start', 'end'))
    _, root = next(context)
    for event, elem in context:
        if event == 'end' and elem.tag in tags:
            yield elem
            root.clear()

#Validating that during creation of CSV files the fields are all in accordance with the columns that should be
#in the CSV files
def validate_element(element, validator, schema=SCHEMA):
    """Raise ValidationError if element does not match schema"""
    if validator.validate(element, schema) is not True:
        field, errors = next(validator.errors.iteritems())
        message_string = "\nElement of type '{0}' has the following errors:\n{1}"
        error_string = pprint.pformat(errors)
        
        raise Exception(message_string.format(field, error_string))


class UnicodeDictWriter(csv.DictWriter, object):
    """Extend csv.DictWriter to handle Unicode input"""

    def writerow(self, row):
        super(UnicodeDictWriter, self).writerow({
            k: (v.encode('utf-8') if isinstance(v, unicode) else v) for k, v in row.iteritems()
        })

    def writerows(self, rows):
        for row in rows:
            self.writerow(row)

# ================================================== #
#       Main Function-Creating the CSV files         #
# ================================================== #
def process_map(file_in, validate):
    """Iteratively process each XML element and write to csv(s)"""

    with codecs.open(NODES_PATH, 'w') as nodes_file, \
         codecs.open(NODE_TAGS_PATH, 'w') as nodes_tags_file, \
         codecs.open(WAYS_PATH, 'w') as ways_file, \
         codecs.open(WAY_NODES_PATH, 'w') as way_nodes_file, \
         codecs.open(WAY_TAGS_PATH, 'w') as way_tags_file:

        nodes_writer = UnicodeDictWriter(nodes_file, NODE_FIELDS)
        node_tags_writer = UnicodeDictWriter(nodes_tags_file, NODE_TAGS_FIELDS)
        ways_writer = UnicodeDictWriter(ways_file, WAY_FIELDS)
        way_nodes_writer = UnicodeDictWriter(way_nodes_file, WAY_NODES_FIELDS)
        way_tags_writer = UnicodeDictWriter(way_tags_file, WAY_TAGS_FIELDS)

        nodes_writer.writeheader()
        node_tags_writer.writeheader()
        ways_writer.writeheader()
        way_nodes_writer.writeheader()
        way_tags_writer.writeheader()

        validator = cerberus.Validator()
        count = 1
        for element in get_element(file_in, tags=('node', 'way')):
            if count % 10000 == 0: #Setting a counter to show how many rows the code has processed
                print count
            count += 1
            el = shape_element(element)
            if el:
                if validate is True:
                    validate_element(el, validator)

                if element.tag == 'node':
                    nodes_writer.writerow(el['node'])
                    node_tags_writer.writerows(el['node_tags'])
                elif element.tag == 'way':
                    ways_writer.writerow(el['way'])
                    way_nodes_writer.writerows(el['way_nodes'])
                    way_tags_writer.writerows(el['way_tags'])

if __name__ == '__main__':
    # Note: If the validation is set to True, the process takes much longer than when it is set to False
    process_map(OSM_PATH, validate=False)


10000
20000
30000
40000
50000
60000
70000
80000
90000
100000
110000
120000
130000
140000
150000
160000
170000
180000
190000
200000
210000
220000
230000
240000
250000
260000
270000
280000
290000
300000
310000
320000
330000
340000
350000
360000
370000
380000
390000
400000
410000
420000
430000
440000
450000
460000
470000
480000
490000
500000
510000
520000
530000
540000
550000
560000
570000
580000
590000
600000
610000
620000
630000
640000
650000
660000
670000
680000
690000
700000
710000
720000
730000
740000
750000
760000
770000
780000
790000
800000
810000
820000
830000
840000
850000
860000
870000
880000
890000
900000
910000
920000
930000
940000
950000
960000
970000
980000
990000
1000000
1010000
1020000
1030000
1040000
1050000
1060000
1070000
1080000
1090000
1100000
1110000
1120000
1130000
1140000
1150000
1160000
1170000
1180000
1190000
1200000
1210000
1220000
1230000
1240000
1250000
1260000
1270000
1280000
1290000
1300000
1310000
1320000
1330000
1340000
1350000
1360000
1370000
1380000
1390

### Creating the database

I have created the database called 'openstreetmap_sf_db' and I created tables with columns based on the columns from the CSV files, and insert the data from the CSV files to the corresponding tables in the database.


In [51]:
import sqlite3
import csv
from pprint import pprint

sqlite_file = 'openstreetmap_sf_db.sqlite'

conn = sqlite3.connect(sqlite_file)
cur = conn.cursor()

#making sure a table that already exists does not get created
cur.execute('DROP TABLE IF EXISTS nodes')
conn.commit()

#creating the table with its column names and their types
cur.execute('''
    CREATE TABLE nodes_tags(id INTEGER, key TEXT, value TEXT, type TEXT)
''')
conn.commit()

with open('nodes_tags.csv', 'rb') as f:
    dr = csv.DictReader(f)
    in_db = [(i['id'], i['key'], i['value'].decode('utf-8'), i['type']) for i in dr]
    
#insert the data
cur.executemany('INSERT INTO nodes_tags(id, key, value, type) VALUES(?, ?, ?, ?);', in_db)
conn.commit()



In [ ]:
cur.execute('SELECT * FROM nodes_tags')
rows = cur.fetchall()
print('1):')
pprint(rows)

1):
[(26028129, u'ref', u'406', u'regular'),
 (26028129,
  u'source',
  u'http://www.dot.ca.gov/hq/traffops/signtech/calnexus/pdf/101.pdf',
  u'regular'),
 (26028129, u'exit_to', u'SR-84;Marsh Road', u'regular'),
 (26028129, u'highway', u'motorway_junction', u'regular'),
 (26029880, u'ref', u'414A', u'regular'),
 (26029880,
  u'source',
  u'http://www.dot.ca.gov/hq/traffops/signtech/calnexus/pdf/101.pdf',
  u'regular'),
 (26029880, u'exit_to', u'Hillsdale Boulevard;Foster City', u'regular'),
 (26029880, u'highway', u'motorway_junction', u'regular'),
 (26819224, u'created_by', u'JOSM', u'regular'),
 (26819236, u'population', u'2010', u'census'),
 (26819236, u'continent', u'North America', u'regular'),
 (26819236, u'country', u'United States', u'regular'),
 (26819236, u'country', u'US', u'regular'),
 (26819236, u'name', u'San Francisco', u'regular'),
 (26819236, u'de', u'San Francisco', u'name'),
 (26819236, u'eu', u'San Francisco', u'name'),
 (26819236,
  u'fa',
  u'\u0633\u0627\u0646 \

In [55]:
conn.close()

In [69]:
conn = sqlite3.connect(sqlite_file)
cur = conn.cursor()

#making sure a table that already exists does not get created
cur.execute('DROP TABLE IF EXISTS nodes')
conn.commit()

#creating the table with its column names and their types
cur.execute('''
    CREATE TABLE ways(id INTEGER PRIMARY KEY, user TEXT, uid INTEGER, version INTEGER, changeset INTEGER, timestamp DATETIME)
''')
conn.commit()

with open('ways.csv', 'rb') as f:
    dr = csv.DictReader(f)
    in_db = [(i['id'], i['user'].decode('utf-8'), i['uid'], i['version'], i['changeset'], i['timestamp']) for i in dr]
    
#insert the data
cur.executemany('INSERT INTO ways(id, user, uid, version, changeset, timestamp) VALUES(?, ?, ?, ?, ?, ?);', in_db)
conn.commit()

In [70]:
cur.execute('SELECT * FROM ways')
rows = cur.fetchall()
print('1):')
pprint(rows)

1):
[(4311275, u'StellanL', 28775, 42, 25770502, u'2014-09-30T15:18:33Z'),
 (4352168, u'n76', 318696, 49, 17945349, u'2013-09-20T19:03:57Z'),
 (4699869, u'StellanL', 28775, 14, 18894823, u'2013-11-14T14:41:06Z'),
 (4699870, u'NE2', 207745, 58, 13288060, u'2012-09-28T17:47:53Z'),
 (4757466, u'JanDG', 1816182, 24, 27996466, u'2015-01-08T13:05:18Z'),
 (4757566, u'Dami_Tn', 2012449, 9, 25064332, u'2014-08-27T23:55:28Z'),
 (4757625, u'markscalf', 2772907, 15, 42458749, u'2016-09-26T23:27:18Z'),
 (4757626, u'NE2', 207745, 9, 12963218, u'2012-09-03T06:39:55Z'),
 (4757680, u'NE2', 207745, 10, 8943068, u'2011-08-07T00:39:51Z'),
 (4757702, u'JanDG', 1816182, 18, 30479822, u'2015-04-25T17:33:35Z'),
 (4757708, u'JanDG', 1816182, 14, 27370650, u'2014-12-10T06:19:29Z'),
 (4758023, u'oba510', 933797, 12, 44994098, u'2017-01-08T06:02:01Z'),
 (4758091, u'oba510', 933797, 14, 45388649, u'2017-01-23T07:58:47Z'),
 (4758092, u'oba510', 933797, 10, 44994098, u'2017-01-08T06:02:00Z'),
 (4758131, u'dannykath'

ValueError: I/O operation on closed file

In [71]:
conn.close()

In [61]:
conn = sqlite3.connect(sqlite_file)
cur = conn.cursor()

#making sure a table that already exists does not get created
cur.execute('DROP TABLE IF EXISTS nodes')
conn.commit()

#creating the table with its column names and their types
cur.execute('''
    CREATE TABLE ways_nodes(id INTEGER, node_id INTEGER, position INTEGER)
''')
conn.commit()

with open('ways_nodes.csv', 'rb') as f:
    dr = csv.DictReader(f)
    in_db = [(i['id'], i['node_id'], i['position']) for i in dr]
    
#insert the data
cur.executemany('INSERT INTO ways_nodes(id, node_id, position) VALUES(?, ?, ?);', in_db)
conn.commit()

In [ ]:
cur.execute('SELECT * FROM ways_nodes')
rows = cur.fetchall()
print('1):')
pprint(rows)

1):
[(4311275, 32927063, 0),
 (4311275, 2262036212, 1),
 (4311275, 30033688, 2),
 (4311275, 989840971, 3),
 (4311275, 989840976, 4),
 (4311275, 2262036223, 5),
 (4311275, 29891969, 6),
 (4311275, 2262493188, 7),
 (4311275, 2262036210, 8),
 (4311275, 989842032, 9),
 (4311275, 2262036209, 10),
 (4311275, 30033691, 11),
 (4311275, 989842035, 12),
 (4311275, 989842036, 13),
 (4311275, 2262036215, 14),
 (4311275, 29891970, 15),
 (4311275, 989842039, 16),
 (4311275, 989842041, 17),
 (4311275, 989842042, 18),
 (4311275, 2262036216, 19),
 (4311275, 30033693, 20),
 (4311275, 2262036213, 21),
 (4311275, 263061076, 22),
 (4311275, 267757896, 23),
 (4311275, 2262036204, 24),
 (4311275, 2262036218, 25),
 (4311275, 1096003001, 26),
 (4311275, 2262036225, 27),
 (4311275, 1096003002, 28),
 (4311275, 2262036203, 29),
 (4311275, 30033694, 30),
 (4311275, 2262036199, 31),
 (4311275, 1096003003, 32),
 (4311275, 2262036222, 33),
 (4311275, 2262036219, 34),
 (4311275, 1096003004, 35),
 (4311275, 29891971, 3

In [224]:
conn.close()

In [63]:
conn = sqlite3.connect(sqlite_file)
cur = conn.cursor()

#making sure a table that already exists does not get created
cur.execute('DROP TABLE IF EXISTS nodes')
conn.commit()

#creating the table with its column names and their types
cur.execute('''
    CREATE TABLE ways_tags(id INTEGER , key TEXT, value TEXT, type TEXT)
''')
conn.commit()

with open('ways_tags.csv', 'rb') as f:
    dr = csv.DictReader(f)
    in_db = [(i['id'], i['key'], i['value'].decode('utf-8'), i['type']) for i in dr]
    
#insert the data
cur.executemany('INSERT INTO ways_tags(id, key, value, type) VALUES(?, ?, ?, ?);', in_db)
conn.commit()

In [225]:
cur.execute('SELECT * FROM ways_tags')
rows = cur.fetchall()
print('1):')
pprint(rows)

1):
[(4311275, u'NHS', u'STRAHNET', u'regular'),
 (4311275, u'hgv', u'designated', u'regular'),
 (4311275, u'ref', u'US 101', u'regular'),
 (4311275, u'name', u'Bayshore Freeway', u'regular'),
 (4311275, u'lanes', u'4', u'regular'),
 (4311275, u'oneway', u'yes', u'regular'),
 (4311275, u'bicycle', u'no', u'regular'),
 (4311275, u'highway', u'motorway', u'regular'),
 (4311275, u'national_network', u'yes', u'hgv'),
 (4311275,
  u'hgv:national_network',
  u'Title 23: Highways Part 658 http://ecfr.gpoaccess.gov/cgi/t/text/text-idx?c=ecfr&rgn=div5&view=text&node=23:1.0.1.7.33&idno=23',
  u'source'),
 (4352168, u'hgv', u'designated', u'regular'),
 (4352168, u'ref', u'I 280', u'regular'),
 (4352168, u'foot', u'no', u'regular'),
 (4352168, u'name', u'Junipero Serra Freeway', u'regular'),
 (4352168, u'horse', u'no', u'regular'),
 (4352168, u'lanes', u'4', u'regular'),
 (4352168, u'oneway', u'yes', u'regular'),
 (4352168, u'bicycle', u'no', u'regular'),
 (4352168, u'highway', u'motorway', u'regu

ValueError: I/O operation on closed file

In [226]:
conn.close()

#### Inserting the data from huge files like 'nodes' into the database

The below code is used to create the tables for the nodes.csv file. Since this file is very big, I am using the code below to split it into various smaller files. Got the code from: https://discussions.udacity.com/t/memory-error-nodes-csv-to-sql-database/186806/10


In [72]:
#importing the nodes.csv file to sqlite3
import sqlite3
import csv
import os
import math
from time import time
from pprint import pprint
from decimal import Decimal

class UploadSplitCSVFiles(object):

    def __init__(self):
        pass

    def rowCountCSV(self,infile):
        import csv
        from time import time

        t0 = time()
        with open(infile) as fin:
            csvin = csv.reader(fin)
            row_count = sum(1 for row in csvin)

        print '{:.<40s}: {:0d}'.format('Number of rows in file: ', row_count)
        print '{:.<40s}: {:.2f} secs'.format('Time taken to count csv file: ', Decimal(time()-t0))
        return row_count


    def splitCSV(self, infile, n):
        """ Splits a csv file into n files
    
        retaining the header row for each file
    
        using the filename as base name numbering each file 
    
        uses rowCountCSV() """
    
        row_count = self.rowCountCSV(infile)
    
        nrow = int(math.ceil(row_count/float(n)))
        i = 1
        j = 1

        name = infile[:infile.find(".")]

        t0 = time()

        with open(infile) as fin:
            csvin = csv.reader(fin)
            header = next(csvin)
    
            for row in csvin:
                if i % nrow == 0 or i == 1:
                    outfile = '{}_{}.csv'.format(name,j)
                    # print outfile
                    fout = open(outfile, 'wb')
                    csvout = csv.writer(fout)
                    csvout.writerow(header)
                    j += 1

                csvout.writerow(row)
                i += 1

        print '{:.<40s}: {:0d}'.format('Number of rows per new file: ', nrow)
        print '{:.<40s}: {:.2f} secs'.format('Time taken to create csv files: ', Decimal(time()-t0))




    def uploadPartCSVFiles(self,dbname,infile,n):
        """ Uploads partitioned CSV files
    
        infile -- name of file partitioned
        n -- number of partitions
    
        The partitioned files must be named:
    
        base_1.csv, base_2.csv, ..., base_n.csv, where base is
        the original filename (without the extension) """
        
        self.splitCSV(infile, n)
    
        sqlite_file = dbname    # name of the sqlite database file

        # Connect to the database
        conn = sqlite3.connect(sqlite_file)

        # Get a cursor object
        cur = conn.cursor()

        cur.execute('''DROP TABLE IF EXISTS nodes;''')
        conn.commit()

        # Create the table, specifying the column names and data types:
        cur.execute('''
            CREATE TABLE IF NOT EXISTS nodes(id INTEGER PRIMARY KEY, lat REAL, 
            lon REAL, user TEXT, uid INTEGER, version TEXT, changeset INTEGER, timestamp DATE)
        ''')
        conn.commit()
        
        t0 = time()


        name = infile[:infile.find(".")]

        for i in range(1, n+1):
            partfile = '{}_{}.csv'.format(name,i)
            # Read in the csv file as a dictionary, format the
            # data as a list of tuples:
            with open(partfile,'rb') as fin:
                dr = csv.DictReader(fin) # comma is default delimiter
                to_db = [(i['id'].decode('utf-8'), i['lat'],i['lon'],i['user'].decode('utf-8'),
                          i['uid'],i['version'],i['changeset'],i['timestamp']) for i in dr]
    

            # insert the formatted data
            cur.executemany("INSERT INTO nodes(id, lat, lon, user, uid, version, changeset, timestamp) VALUES (?, ?, ?, ?,?, ?, ?, ?);", to_db)
            conn.commit()

        print '{:.<40s}: {:.0f} MB'.format('The original csv file size is',os.path.getsize(infile)/1.0e6)
        print '{:.<40s}: {:.0f} MB'.format('The database file size is',os.path.getsize(dbname)/1.0e6)
        print '{:.<40s}: {:.2f} secs'.format('Time taken to upload csv files: ', Decimal(time()-t0))        
        
        conn.close()

In [73]:
from UploadSplitCSVFiles import UploadSplitCSVFiles

uploadSplit = UploadSplitCSVFiles()

uploadSplit.uploadPartCSVFiles('openstreetmap_sf_db.sqlite','nodes.csv',30)

Number of rows in file: ................: 4714878
Time taken to count csv file: ..........: 8.15 secs
Number of rows per new file: ...........: 157163
Time taken to create csv files: ........: 27.67 secs
The original csv file size is...........: 397 MB
The database file size is...............: 541 MB
Time taken to upload csv files: ........: 99.66 secs


In [105]:
conn.close()

### Getting queries based on the data in the database

In [238]:
from pprint import pprint
import os
from hurry.filesize import size

dirpath = '/Users/nazaninmirarab/Desktop/Data Science/P3/Project/Sizes'

files_list = []
for path, dirs, files in os.walk(dirpath):
    files_list.extend([(filename, size(os.path.getsize(os.path.join(path, filename)))) for filename in files])

for filename, size in files_list:
    print '{:.<40s}: {:5s}'.format(filename,size)

 nodes.csv...............................: 378M 
nodes_tags.csv..........................: 8M   
openstreetmap_sf_db.sqlite..............: 515M 
san-francisco_california.osm............: 966M 
ways.csv................................: 31M  
ways_nodes.csv..........................: 128M 
ways_tags.csv...........................: 48M  


In [242]:
con = sqlite3.connect(sqlite_file)
cur = con.cursor()

def number_of_nodes():
    output = cur.execute('SELECT COUNT(*) FROM nodes')
    return output.fetchone()[0]

def number_of_ways():
    output = cur.execute('SELECT COUNT(*) FROM ways')
    return output.fetchone()[0]

def number_of_unique_users():
    output = cur.execute('SELECT COUNT(DISTINCT e.uid) FROM \
                         (SELECT uid FROM nodes UNION ALL SELECT uid FROM ways) e')
    return output.fetchone()[0]

print 'Number of nodes:..........' , number_of_nodes()
print 'Number of ways:...........' , number_of_ways()
print 'Number of unique users:...' , number_of_unique_users()

 Number of nodes:.......... 4714877
Number of ways:........... 551145
Number of unique users:... 2579


In [253]:
def most_contributing_users():
    
    output = cur.execute('SELECT e.user, COUNT(*) as num FROM \
                         (SELECT user FROM nodes UNION ALL SELECT user FROM ways) e \
                         GROUP BY e.user \
                         ORDER BY num DESC \
                         LIMIT 10 ')
    pprint(output.fetchall())
    return output.fetchall()

print 'Most contributing users: \n'
number_of_most_contributing_users()


Most contributing users: 



[(u'ediyes', 918915),
 (u'Luis36995', 710456),
 (u'Rub21', 395077),
 (u'RichRico', 224724),
 (u'calfarome', 185498),
 (u'oldtopos', 167538),
 (u'KindredCoda', 151208),
 (u'karitotp', 135330),
 (u'samely', 125861),
 (u'abel801', 108313)]

In [247]:
def number_of_users_contributed_once():
    
    output = cur.execute('SELECT COUNT(*) FROM \
                             (SELECT e.user, COUNT(*) as num FROM \
                                 (SELECT user FROM nodes UNION ALL SELECT user FROM ways) e \
                                  GROUP BY e.user \
                                  HAVING num = 1) u')
    
    return output.fetchone()[0]
                         
print 'Number of users who have contributed once: \n', number_of_users_contributed_once()

Number of users who have contributed once: 
634


In [264]:
def top_ten_amenities_in_sf():
    output = cur.execute('SELECT value, COUNT(*) as num FROM nodes_tags\
                            WHERE key="amenity" \
                            GROUP BY value \
                            ORDER BY num DESC \
                            LIMIT 20' )
    pprint(output.fetchall())
    return output.fetchall()

print 'Top ten amenities: \n'
top_ten_amenities_in_sf()

Top ten amenities: 

[(u'restaurant', 2816),
 (u'bench', 1137),
 (u'cafe', 943),
 (u'place_of_worship', 719),
 (u'post_box', 680),
 (u'school', 604),
 (u'fast_food', 562),
 (u'bicycle_parking', 556),
 (u'drinking_water', 492),
 (u'toilets', 394),
 (u'bank', 364),
 (u'bar', 314),
 (u'parking', 272),
 (u'fuel', 270),
 (u'car_sharing', 225),
 (u'waste_basket', 203),
 (u'pub', 200),
 (u'atm', 189),
 (u'post_office', 156),
 (u'pharmacy', 143)]


[]

In [266]:
def cuisines_in_sf():
    output = cur.execute ('SELECT value, COUNT(*) as num FROM ways_tags \
                           WHERE key="cuisine" \
                           GROUP BY value \
                           ORDER BY num DESC \
                           LIMIT 10')
    pprint(output.fetchall())
    return output.fetchall()

print 'Top 10 cuisines: \n'
cuisines_in_sf()


Top 10 cuisines: 

[(u'burger', 71),
 (u'mexican', 47),
 (u'pizza', 29),
 (u'chinese', 26),
 (u'american', 20),
 (u'coffee_shop', 19),
 (u'italian', 15),
 (u'japanese', 15),
 (u'sushi', 12),
 (u'seafood', 10)]


[]

In [259]:
def shops_in_sf():
    output = cur.execute('SELECT value, COUNT(*) as num FROM nodes_tags\
                            WHERE key="shop" \
                            GROUP BY value \
                            ORDER BY num DESC' )
    pprint.pprint(output.fetchall())
    return output.fetchall()

print 'Different types of shops: \n'
top_ten_amenities_in_sf()

Different types of shops: 



[(u'restaurant', 2816),
 (u'bench', 1137),
 (u'cafe', 943),
 (u'place_of_worship', 719),
 (u'post_box', 680),
 (u'school', 604),
 (u'fast_food', 562),
 (u'bicycle_parking', 556),
 (u'drinking_water', 492),
 (u'toilets', 394),
 (u'bank', 364),
 (u'bar', 314),
 (u'parking', 272),
 (u'fuel', 270),
 (u'car_sharing', 225),
 (u'waste_basket', 203),
 (u'pub', 200),
 (u'atm', 189),
 (u'post_office', 156),
 (u'pharmacy', 143)]

In [265]:
def users_who_added_amenity():
    output = cur.execute('SELECT DISTINCT(nodes.user), nodes_tags.value FROM \
                            nodes join nodes_tags \
                            on nodes.id=nodes_tags.id \
                            WHERE key="amenity" \
                            GROUP BY value' )
    pprint(output.fetchall())
    return output.fetchall()

print 'Users who added amenity to the map: \n'
users_who_added_amenity()

Users who added amenity to the map: 

[(u'claysmalley', u'Corner Market'),
 (u'dchiles', u'Note 281478'),
 (u'lxbarth', u'Pet grooming shop'),
 (u'oldtopos', u'addr:housenumber'),
 (u'JessAk71', u'amusements'),
 (u'Mark Mavromatis', u'animal_shelter'),
 (u'Jothirnadh', u'arts_centre'),
 (u'manings', u'atm'),
 (u'JessAk71', u'bakery'),
 (u'poornibadrinath', u'bank'),
 (u'Fa7C0N', u'bar'),
 (u'JessAk71', u'barber'),
 (u'Alx303', u'bbq'),
 (u'enveloper', u'bench'),
 (u'jstratm', u'bicycle_parking'),
 (u'blazinglauren', u'bicycle_rental'),
 (u'Dero Bike Racks', u'bicycle_repair_station'),
 (u'dchiles', u'biergarten'),
 (u'Alps Pierrat', u'boat_rental'),
 (u'Gregory Arenius', u'brokerage'),
 (u'manings', u'bureau_de_change'),
 (u'claysmalley', u'bus_station'),
 (u'poornibadrinath', u'cafe'),
 (u'SomeoneElse_Revert', u'candy_store'),
 (u'manings', u'car_rental'),
 (u'JessAk71', u'car_share'),
 (u'JessAk71', u'car_sharing'),
 (u'AndrewSnow', u'car_wash'),
 (u'balrog-kun', u'carpool'),
 (u'Dav

[]

### Additional suggestions for improving and analyzing the data

It's obvious that some common practices for inputting data in the map is not being followed by every user. One bold example of this was users without a user id. Lack of such information can later make the data investigation inaccurate as not all the correct data is provided. It could be better if adding user's information would be a mandatory step.
